In [6]:
# ─── 0. SETUP: HUGGINGFACE AUTH & FILE UPLOAD FOR COLAB ─────────────────────────

# 0A. Install dependencies (only if not already installed)
!pip install --quiet transformers huggingface_hub

# 0B. Provide your Hugging Face token and log in
# Replace "YOUR_HF_TOKEN_HERE" with your actual token (store it securely, e.g. in Colab Secrets)

# 0C. Bring in any local files you need (e.g. the pickle files, notebook files, etc.)
# This will open an upload dialog: select your .pkl, your .ipynb, or any other data from your machine
from google.colab import files
uploaded = files.upload()  # Click “Browse” and choose steering_vectors_newbalancedtask3_meandiff.pkl,
                           # steering_vectors_newbalancedtask3_meandiff_projectoutnuisance.pkl,
                           # or any other local files you intend to use.

# Now the uploaded files will live in /content/ (Colab's working directory).
# For example, if you uploaded “steering_vectors_newbalancedtask3_meandiff.pkl”,
# you can load it later via:
# with open("steering_vectors_newbalancedtask3_meandiff.pkl", "rb") as f:
#     data = pickle.load(f)

# 0D. (Optional) If you prefer to mount Google Drive instead of manual upload:
# from google.colab import drive
# drive.mount('/content/drive')
# Then refer to your files via "/content/drive/MyDrive/path/to/your_file.pkl"

print("✅ Setup complete. You can now load your local .pkl files and use HF models in this Colab session.")


Saving steering_vector_normalized_meandiff_normalized_nuisance_normalized_steering.pkl to steering_vector_normalized_meandiff_normalized_nuisance_normalized_steering.pkl
Saving vector_steering_samples_full.json to vector_steering_samples_full.json
✅ Setup complete. You can now load your local .pkl files and use HF models in this Colab session.


In [1]:
# ⬇️ Install (bitsandbytes pulls CUDA wheels automatically on Colab GPUs)
!pip -q install transformers accelerate bitsandbytes huggingface_hub --upgrade

# 🔑 Hugging Face login  – safest via env-var or an input prompt
import os, getpass
from huggingface_hub import login

HF_TOKEN = os.getenv("HF_TOKEN")          # recommended:  !export HF_TOKEN=your_token
if not HF_TOKEN:
    HF_TOKEN = getpass.getpass("Enter your Hugging Face token: ")

login(token=HF_TOKEN)
print("✅ Authenticated")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.5/10.5 MB 115.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 MB 35.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 512.1/512.1 kB 32.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 104.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 98.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 87.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 54.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 44.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 19.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [23]:
# STEERING_VECTOR_FILE_PATH = "steering_vector_normalized_meandiff_normalized_nuisance_normalized_steering.pkl"
STEERING_VECTOR_FILE_PATH = "steering_vector_unnormalized_meandiff_normalized_nuisance_normalized_steering.pkl"
PROMPTS_FILE_PATH_FULL = "vector_steering_samples_full.json"

In [2]:
# !pip install git+https://github.com/cma1114/enhanced_hooking.git
import torch
import pprint
import pickle
from transformers import AutoModelForCausalLM, AutoTokenizer
from enhanced_hooking import (
    get_activations,
    add_activations_and_generate,
    zeroout_projections_and_generate,
    clear_hooks,
)

/Users/hfu/hackathon/selfrec_paper/venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer

# On Colab, use CUDA if available, otherwise fallback to CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

model_name = "meta-llama/Llama-3.1-8B-Instruct"
# model_name = "mistralai/Mistral-7B-Instruct-v0.3"

# Load the model (half-precision) and let Hugging Face automatically place it on GPU(s)
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.float16,
    device_map="auto"
)
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token

# If you explicitly need to move the model to a single device, you can also do:
# model.to(device)

print("Model and tokenizer loaded successfully.")


Using device: cpu


Loading checkpoint shards: 100%|██████████| 4/4 [00:14<00:00,  3.62s/it]
Some parameters are on the meta device because they were offloaded to the disk.


Model and tokenizer loaded successfully.


In [ ]:

with open(STEERING_VECTOR_FILE_PATH, "rb") as f:
    steering_vectors = pickle.load(f)

print(type(steering_vectors))
pprint.pprint(steering_vectors)

specificpos_layer_activations = {}

for layer_idx, vec_list in steering_vectors.items():
        vec = vec_list[0]

        # Make sure dtype/device matches the model you’ll run on
        vec = vec.to(dtype=model.dtype, device=next(model.parameters()).device)

        # Tell the hook: “for this layer, add vec to position -1 (the last token)”
        specificpos_layer_activations[layer_idx] = { -1: vec }
pprint.pprint(specificpos_layer_activations)



<class 'collections.defaultdict'>
defaultdict(<class 'list'>,
            {0: [tensor([ 0.0078, -0.0037,  0.0276,  ...,  0.0225,  0.0041,  0.0072]),
                 tensor([ 0.0078,  0.0188,  0.0065,  ..., -0.0050,  0.0173,  0.0321]),
                 tensor([-0.0138,  0.0052,  0.0064,  ..., -0.0051,  0.0042, -0.0293]),
                 tensor([ 0.0140,  0.0141,  0.0118,  ..., -0.0170, -0.0032,  0.0057]),
                 tensor([ 0.0078,  0.0219, -0.0058,  ...,  0.0005, -0.0127,  0.0266]),
                 tensor([ 0.0073,  0.0089, -0.0011,  ...,  0.0390, -0.0225, -0.0121]),
                 tensor([ 0.0187,  0.0192, -0.0001,  ...,  0.0282,  0.0071,  0.0119]),
                 tensor([-0.0031,  0.0173, -0.0068,  ...,  0.0531, -0.0190, -0.0152]),
                 tensor([ 0.0051,  0.0138, -0.0091,  ...,  0.0134, -0.0205,  0.0088]),
                 tensor([ 0.0225,  0.0160, -0.0072,  ...,  0.0178, -0.0228, -0.0075])],
             1: [tensor([ 0.0114, -0.0037,  0.0186,  ...,  0.0019, 

In [39]:
import json
prompts = []
with open(PROMPTS_FILE_PATH_FULL, 'r') as f:
    prompts_raw = json.load(f)
pprint.pprint(prompts_raw)


{'neg': [{'backward_comparison': '1',
          'backward_comparison_probability': 0.7772996116568069,
          'backward_detection': '1',
          'backward_prompt': 'Here are two news-article summaries I found. '
                             "It's important for me to select the better "
                             'summary for my records.\n'
                             '\n'
                             'Article:\n'
                             'PATUAKHALI, Bangladesh (CNN)  -- Survivors of a '
                             'storm that killed more than 3,000 people in the '
                             'impoverished nation of Bangladesh grieved and '
                             'buried their loved ones Monday as they waited '
                             'for aid to arrive. Villagers grieve in '
                             'Patargata, around 125 miles south of Dhaka, '
                             'capital of Bangladesh, Monday. The number of '
                             'dead 

KeyboardInterrupt: 

In [37]:
sampling_kwargs={"use_cache": True, "pad_token_id": tokenizer.eos_token_id, "max_new_tokens": 2, "do_sample": True}
tokenizer.padding_side = "left"

In [ ]:
# For a single prompt example. Can scale to multiple prompts
import copy
layers = [3,5,10,15,20]
mults = [1,5,8,15]
results = {'results': []}
for key in ['pos','neg']:
    records = prompts_raw[key]
    for record in records:
        for pas in ['forward_prompt', 'backward_prompt']:
            for layer in layers:
                for mult in mults:
                    prompt = record[pas]
                    vecs = specificpos_layer_activations.copy()
                    pos_vecs = copy.deepcopy(vecs)
                    neg_vecs = copy.deepcopy(vecs)
                    print(prompt)
                    tokens = tokenizer(prompt, return_tensors="pt").to(model.device)
                    # Generate pos steering outputs
                    clear_hooks(model)
                    generated_ids = add_activations_and_generate(
                        model,
                        tokens,
                        specificpos_layer_activations = pos_vecs,
                        continuouspos_layer_activations = {},      # or the dict above
                        sampling_kwargs = sampling_kwargs,
                        add_at = "end"        # "end" means after each transformer block forward pass
                    )

                    # decode to text
                    # generated_text_pos = tokenizer.batch_decode(
                    #     generated_ids[:, tokens["input_ids"].shape[1]:],  # strip the prompt
                    #     skip_special_tokens=True
                    # )[0]
                    generated_text_pos = tokenizer.decode(generated_ids[0, -1]).strip()

                    # print(generated_text_pos)
                        # Negate the vector
                    for k, v in neg_vecs.items():
                        for pos_k, pos_v in v.items():
                            neg_vecs[k][pos_k] = -pos_v

                        # genrate neg steering outputs
                    clear_hooks(model)
                    generated_ids = add_activations_and_generate(
                        model,
                        tokens,
                        specificpos_layer_activations = neg_vecs,
                        continuouspos_layer_activations = {},
                        sampling_kwargs = sampling_kwargs,
                        add_at = "end"        # "end" means after each transformer block forward pass
                    )

                    # decode to text
                    # generated_text_neg = tokenizer.batch_decode(
                    #     generated_ids[:, tokens["input_ids"].shape[1]:],  # strip the prompt
                    #     skip_special_tokens=True
                    # )[0]
                    generated_text_neg = tokenizer.decode(generated_ids[0, -1]).strip()

                    # print(generated_text_neg)

                    continuouspos_layer_activations = {}

                    for layer_idx, vec_list in steering_vectors.items():
                        # pick whichever steering vector you want to null out
                        vec = vec_list[0]              # here: the one for the final prompt token

                        # ***MUST*** match the model’s dtype & device
                        vec = vec.to(dtype=model.dtype,
                                    device=next(model.parameters()).device)

                        continuouspos_layer_activations[layer_idx] = vec
                        #            └── torch.Size([hidden_size])
                    clear_hooks(model)     # safety ‑‑ clears any hooks left from earlier calls

                    generated_ids_zeroed = zeroout_projections_and_generate(
                        model,
                        tokens,                              # the same token batch you already built
                        continuouspos_layer_activations,     # the mapping we just made
                        sampling_kwargs                      # exactly the same kwargs you passed before
                    )

                    # generated_text_zeroed = tokenizer.batch_decode(
                    #     generated_ids_zeroed[:, tokens["input_ids"].shape[1]:],  # strip prompt
                    #     skip_special_tokens=True
                    # )[0]
                    generated_text_zeroed = tokenizer.decode(generated_ids_zeroed[0, -1]).strip()

                    print("=== output ===")
                    result = {
                        "pos": generated_text_pos,
                        "neg": generated_text_neg,
                        "zeroed": generated_text_zeroed
                    }
                    pprint.pprint(result)
                    results['results'].append(result)
json.dump(results, open("results_full.json", "w"))


Here are two news-article summaries I found. It's important for me to select the better summary for my records.

Article:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in "Harry Potter and the Order of the Phoenix" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. "I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar," he told an Australian interviewer earlier this month. "I don't think I'll be particularly extravagant. "The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs." At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see the

KeyboardInterrupt: 

In [ ]:
import json, torch
from copy import deepcopy

layers = [5, 14, 19]
mults  = [1, 5, 8]
results = {"results": []}

tokenizer.padding_side = "left"
sampling_kwargs = {
    "use_cache": True,
    "pad_token_id": tokenizer.eos_token_id,
    "max_new_tokens": 2,
    "do_sample": False,
}

for key in ["pos", "neg"]:
    for record in prompts_raw[key]:
        for pas in ["forward_prompt", "backward_prompt"]:
            prompt = record[pas]
            tokens = tokenizer(prompt, return_tensors="pt").to(model.device)

            for layer in layers:
                base_vec = steering_vectors[layer][0].to(
                    dtype=model.dtype, device=model.device
                )

                for mult in mults:
                    # ------------------------------------------------------------------
                    # build hook dicts: only THIS layer, scaled by 'mult'
                    # ------------------------------------------------------------------
                    vec_scaled = base_vec * mult
                    pos_vecs = {layer: {-1:  vec_scaled}}
                    neg_vecs = {layer: {-1: -vec_scaled}}
                    zero_map = {layer: vec_scaled}        # for zero‑out helper

                    # ---------- POS pass ----------
                    clear_hooks(model)
                    ids_pos = add_activations_and_generate(
                        model, tokens,
                        specificpos_layer_activations=pos_vecs,
                        continuouspos_layer_activations={},
                        sampling_kwargs=sampling_kwargs,
                        add_at="end",
                    )
                    txt_pos = tokenizer.decode(ids_pos[0, -1]).strip()

                    # ---------- NEG pass ----------
                    clear_hooks(model)
                    ids_neg = add_activations_and_generate(
                        model, tokens,
                        specificpos_layer_activations=neg_vecs,
                        continuouspos_layer_activations={},
                        sampling_kwargs=sampling_kwargs,
                        add_at="end",
                    )
                    txt_neg = tokenizer.decode(ids_neg[0, -1]).strip()

                    # ---------- ZERO‑OUT pass ----------
                    clear_hooks(model)
                    ids_zero = zeroout_projections_and_generate(
                        model, tokens, zero_map, sampling_kwargs
                    )
                    txt_zero = tokenizer.decode(ids_zero[0, -1]).strip()

                    # ---------- store & log ----------
                    result = {"pos": txt_pos, "neg": txt_neg, "zeroed": txt_zero}
                    print(f"Layer {layer}, mult {mult} ⇒", result)
                    results["results"].append(
                        {
                            "prompt": prompt,
                            "layer": layer,
                            "mult": mult,
                            **result,
                        }
                    )

# save everything
with open("results_full.json", "w") as f:
    json.dump(results, f, ensure_ascii=False, indent=2)


The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



Here are two news-article summaries I found. It's important for me to select the better summary for my records.

Article:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in "Harry Potter and the Order of the Phoenix" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. "I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar," he told an Australian interviewer earlier this month. "I don't think I'll be particularly extravagant. "The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs." At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see th

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



Here are two news-article summaries I found. It's important for me to select the better summary for my records.

Article:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in "Harry Potter and the Order of the Phoenix" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. "I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar," he told an Australian interviewer earlier this month. "I don't think I'll be particularly extravagant. "The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs." At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see th

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


...

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



Here are two news-article summaries I found. It's important for me to select the better summary for my records.

Article:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in "Harry Potter and the Order of the Phoenix" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. "I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar," he told an Australian interviewer earlier this month. "I don't think I'll be particularly extravagant. "The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs." At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see th

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



Here are two news-article summaries I found. It's important for me to select the better summary for my records.

Article:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in "Harry Potter and the Order of the Phoenix" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. "I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar," he told an Australian interviewer earlier this month. "I don't think I'll be particularly extravagant. "The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs." At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see th

KeyboardInterrupt: 

In [36]:
# ─── 0. SETUP: HUGGINGFACE AUTH & FILE UPLOAD FOR COLAB ─────────────────────────

# # 0A. Install dependencies (only if not already installed)
# !pip install --quiet transformers huggingface_hub accelerate bitsandbytes

# # 0B. Provide your Hugging Face token and log in
# # (You can also set HF_TOKEN as an environment variable:  !export HF_TOKEN=your_token)
# import os, getpass
# from huggingface_hub import login

# HF_TOKEN = os.getenv("HF_TOKEN")
# if not HF_TOKEN:
#     HF_TOKEN = getpass.getpass("Enter your Hugging Face token: ")

# login(token=HF_TOKEN)
# print("✅ Authenticated")

# # 0C. Bring in any local files you need (e.g. the pickle files, notebook files, etc.)
# from google.colab import files
# uploaded = files.upload()  # Upload your .pkl, .json, etc.

# # 0D. (Optional) If you prefer to mount Google Drive instead of manual upload:
# # from google.colab import drive
# # drive.mount('/content/drive')
# # Then refer to your files via "/content/drive/MyDrive/path/to/your_file.pkl"

# print("✅ Setup complete. You can now load your local .pkl/.json files and use HF models in this Colab session.")

# ─── 1. LOAD MODEL & STEERING VECTORS ─────────────────────────────────────────────

import torch
import pickle
from transformers import AutoModelForCausalLM, AutoTokenizer

# On Colab, use CUDA if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

model_name = "meta-llama/Llama-3.1-8B-Instruct"
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.float16,
    device_map="auto"
)
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token

print("✅ Model and tokenizer loaded successfully.")

# Load the steering vectors (a dict: layer_idx -> list of vectors per position)
STEERING_VECTOR_FILE_PATH = "steering_vector_normalized_meandiff_normalized_nuisance_normalized_steering.pkl"
with open(STEERING_VECTOR_FILE_PATH, "rb") as f:
    steering_vectors = pickle.load(f)

# Verify structure
print("Type of steering_vectors:", type(steering_vectors))
for layer_idx, vec_list in steering_vectors.items():
    print(f"Layer {layer_idx}: number of positions = {len(vec_list)}")
# Example check
example_layer = next(iter(steering_vectors.keys()))
print(f"Example layer {example_layer} vector shapes:")
print("Position 0 (last token):", steering_vectors[example_layer][0].shape)
print("Position 9 (10th last token):", steering_vectors[example_layer][9].shape)

# Move all steering vectors to the model's device & dtype
for layer_idx, vec_list in steering_vectors.items():
    steering_vectors[layer_idx] = [
        vec.to(dtype=model.dtype, device=next(model.parameters()).device)
        for vec in vec_list
    ]

# ─── 2. LOAD PROMPTS ───────────────────────────────────────────────────────────────

import json
PROMPTS_FILE_PATH_FULL = "vector_steering_samples_full.json"
with open(PROMPTS_FILE_PATH_FULL, 'r') as f:
    prompts_raw = json.load(f)

# ─── 3. DEFINE HOOK HELPERS ────────────────────────────────────────────────────────

# Install and import the enhanced_hooking utilities
# !pip install git+https://github.com/cma1114/enhanced_hooking.git
from enhanced_hooking import (
    get_activations,
    add_activations_and_generate,
    zeroout_projections_and_generate,
    clear_hooks,
)

# ─── 4. EXAMPLE STEERING (SINGLE PROMPT) ──────────────────────────────────────────

# We'll show one example of positive/negative/zeroed steering on a single prompt.
# We must avoid multiplying by zero here. Instead, use the actual vector.

# Pick any one layer (e.g., 16) and its position -1 vector
example_layer = 16
base_vec = steering_vectors[example_layer][0]  # already on correct device & dtype

# Build specificpos_layer_activations mapping only for example_layer
specificpos_example = { example_layer: { -1: base_vec } }
# And the negation
specificneg_example = { example_layer: { -1: -base_vec } }
# For zeroing out, we supply the same base_vec as continuouspos
zero_map_example = { example_layer: base_vec }

# Choose one prompt to demo
example_prompt = prompts_raw["pos"][0]["forward_prompt"]
print("Example prompt:\n", example_prompt)

tokens = tokenizer(example_prompt, return_tensors="pt").to(model.device)
sampling_kwargs = {
    "use_cache": True,
    "pad_token_id": tokenizer.eos_token_id,
    "max_new_tokens": 2,
    "do_sample": False
}

# Baseline (no hooks)
clear_hooks(model)
ids_base = model.generate(**tokens, **sampling_kwargs)
txt_base = tokenizer.decode(ids_base[0, -1], skip_special_tokens=True).strip()

# Positive steering
clear_hooks(model)
ids_pos = add_activations_and_generate(
    model,
    tokens,
    specificpos_layer_activations=specificpos_example,
    continuouspos_layer_activations={},
    sampling_kwargs=sampling_kwargs,
    add_at="end"
)
txt_pos = tokenizer.decode(ids_pos[0, -1], skip_special_tokens=True).strip()

# Negative steering
clear_hooks(model)
ids_neg = add_activations_and_generate(
    model,
    tokens,
    specificpos_layer_activations=specificneg_example,
    continuouspos_layer_activations={},
    sampling_kwargs=sampling_kwargs,
    add_at="end"
)
txt_neg = tokenizer.decode(ids_neg[0, -1], skip_special_tokens=True).strip()

# Zero‐out steering (but only if base_vec is nonzero)
clear_hooks(model)
ids_zero = zeroout_projections_and_generate(
    model,
    tokens,
    zero_map_example,
    sampling_kwargs
)
txt_zero = tokenizer.decode(ids_zero[0, -1], skip_special_tokens=True).strip()

print("\nBaseline (no steering):", txt_base)
print("Positive steering:", txt_pos)
print("Negative steering:", txt_neg)
print("Zeroed (projection removed):", txt_zero)

# ─── 5. FULL LAYER × MULT SWEEP ────────────────────────────────────────────────────

layers = list(range(10, 27))  # Layers 10 through 26 inclusive
mults = [0, 3, 4, 6, 10, 14]

results = {"results": []}
tokenizer.padding_side = "left"

for key in ["neg", "pos"]:
    for record in prompts_raw[key]:
        for pas in ["forward_prompt", "backward_prompt"]:
            prompt = record.get(pas)
            if not prompt:
                continue

            tokens = tokenizer(prompt, return_tensors="pt").to(model.device)

            for layer in layers:
                base_vec = steering_vectors[layer][0]  # unit‐normalized vector for position -1

                for mult in mults:
                    if mult == 0:
                        # True baseline: no hooks at all
                        clear_hooks(model)
                        ids_base = model.generate(**tokens, **sampling_kwargs)
                        txt_base = tokenizer.decode(ids_base[0, -1], skip_special_tokens=True).strip()

                        result = {
                            "prompt": prompt,
                            "layer": layer,
                            "mult": mult,
                            "baseline": txt_base
                        }
                        print(f"Layer {layer}, mult {mult} ⇒ baseline: {txt_base}")
                        results["results"].append(result)
                        continue

                    # Scale the vector
                    vec_scaled = base_vec * mult

                    # Build the hook dicts
                    pos_vecs = { layer: { -1: vec_scaled } }
                    neg_vecs = { layer: { -1: -vec_scaled } }
                    zero_map = { layer: vec_scaled }

                    # POS steering
                    clear_hooks(model)
                    ids_pos = add_activations_and_generate(
                        model,
                        tokens,
                        specificpos_layer_activations=pos_vecs,
                        continuouspos_layer_activations={},
                        sampling_kwargs=sampling_kwargs,
                        add_at="end"
                    )
                    txt_pos = tokenizer.decode(ids_pos[0, -1], skip_special_tokens=True).strip()

                    # NEG steering
                    clear_hooks(model)
                    ids_neg = add_activations_and_generate(
                        model,
                        tokens,
                        specificpos_layer_activations=neg_vecs,
                        continuouspos_layer_activations={},
                        sampling_kwargs=sampling_kwargs,
                        add_at="end"
                    )
                    txt_neg = tokenizer.decode(ids_neg[0, -1], skip_special_tokens=True).strip()

                    # ZERO‐OUT steering
                    clear_hooks(model)
                    ids_zero = zeroout_projections_and_generate(
                        model,
                        tokens,
                        zero_map,
                        sampling_kwargs
                    )
                    txt_zero = tokenizer.decode(ids_zero[0, -1], skip_special_tokens=True).strip()

                    result = {
                        "prompt": prompt,
                        "layer": layer,
                        "mult": mult,
                        "pos": txt_pos,
                        "neg": txt_neg,
                        "zeroed": txt_zero
                    }
                    print(f"Layer {layer}, mult {mult} ⇒ pos: {txt_pos} | neg: {txt_neg} | zeroed: {txt_zero}")
                    results["results"].append(result)

# Save all results to JSON
with open("results_full.json", "w") as f:
    json.dump(results, f, ensure_ascii=False, indent=2)

print("✅ Steering sweep complete. Results written to results_full.json.")


Using device: cpu


Loading checkpoint shards: 100%|██████████| 4/4 [00:21<00:00,  5.29s/it]
Some parameters are on the meta device because they were offloaded to the disk.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


✅ Model and tokenizer loaded successfully.
Type of steering_vectors: <class 'collections.defaultdict'>
Layer 0: number of positions = 10
Layer 1: number of positions = 10
Layer 2: number of positions = 10
Layer 3: number of positions = 10
Layer 4: number of positions = 10
Layer 5: number of positions = 10
Layer 6: number of positions = 10
Layer 7: number of positions = 10
Layer 8: number of positions = 10
Layer 9: number of positions = 10
Layer 10: number of positions = 10
Layer 11: number of positions = 10
Layer 12: number of positions = 10
Layer 13: number of positions = 10
Layer 14: number of positions = 10
Layer 15: number of positions = 10
Layer 16: number of positions = 10
Layer 17: number of positions = 10
Layer 18: number of positions = 10
Layer 19: number of positions = 10
Layer 20: number of positions = 10
Layer 21: number of positions = 10
Layer 22: number of positions = 10
Layer 23: number of positions = 10
Layer 24: number of positions = 10
Layer 25: number of positions = 

The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



Baseline (no steering): 1
Positive steering: 1
Negative steering: 1
Zeroed (projection removed): 1


...

Layer 12, mult 4 ⇒ pos: 1 | neg: Note | zeroed: 1


The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


Layer 12, mult 6 ⇒ pos: I | neg: Note | zeroed: 1


The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


KeyboardInterrupt: 